In [ ]:
import re
from pathlib import Path
import string
from functools import reduce
from math import log
import itertools

In [ ]:
# Enter smoothing or no smoothing.
smoothing = 1
filename = "textfile.txt"

In [ ]:
# Loads file
# input - filename.txt
# returns a list of sentences seperated by newline in the textfile.
def load_file(filename):
    with open(filename, 'r') as file:
        lines = file.read().split('\n')
    return lines
a=load_file(filename)
a

['[ moby dick by herman melville 1851 ]',
 'etymology .',
 '( supplied by a late consumptive usher to a grammar school )',
 'the pale usher -- threadbare in coat , heart , body , and brain ; i see him now .',
 'he was ever dusting his old lexicons and grammars , with a queer handkerchief , mockingly embellished with all the gay flags of all the known nations of the world .',
 'he loved to dust his old grammars ; it somehow mildly reminded him of his mortality .',
 '" while you take in hand to school others , and to teach them by what name a whale - fish is to be called in our tongue leaving out , through ignorance , the letter h , which almost alone maketh the signification of the word , you deliver that which is not true ."',
 '-- hackluyt',
 '" whale .',
 '... sw . and dan .',
 'hval .',
 'this animal is named from roundness or rolling ; for in dan .',
 'hvalt is arched or vaulted ."',
 "-- webster ' s dictionary",
 '" whale .',
 '...',
 'it is more immediately from the dut .',
 'and

In [ ]:
# Tokenizes the sentences meaning split the sentences into words seperated by the "white sapce".
# input - List of sentences
# returns a list of lists of each sentence being tokenized.
def tokenize_sentence(lines):
    tokenized_lines = [line.split() for line in lines]
    return tokenized_lines
b=tokenize_sentence(a)
b

[['[', 'moby', 'dick', 'by', 'herman', 'melville', '1851', ']'],
 ['etymology', '.'],
 ['(',
  'supplied',
  'by',
  'a',
  'late',
  'consumptive',
  'usher',
  'to',
  'a',
  'grammar',
  'school',
  ')'],
 ['the',
  'pale',
  'usher',
  '--',
  'threadbare',
  'in',
  'coat',
  ',',
  'heart',
  ',',
  'body',
  ',',
  'and',
  'brain',
  ';',
  'i',
  'see',
  'him',
  'now',
  '.'],
 ['he',
  'was',
  'ever',
  'dusting',
  'his',
  'old',
  'lexicons',
  'and',
  'grammars',
  ',',
  'with',
  'a',
  'queer',
  'handkerchief',
  ',',
  'mockingly',
  'embellished',
  'with',
  'all',
  'the',
  'gay',
  'flags',
  'of',
  'all',
  'the',
  'known',
  'nations',
  'of',
  'the',
  'world',
  '.'],
 ['he',
  'loved',
  'to',
  'dust',
  'his',
  'old',
  'grammars',
  ';',
  'it',
  'somehow',
  'mildly',
  'reminded',
  'him',
  'of',
  'his',
  'mortality',
  '.'],
 ['"',
  'while',
  'you',
  'take',
  'in',
  'hand',
  'to',
  'school',
  'others',
  ',',
  'and',
  'to',
  'te

In [ ]:
# Prepare the data for training the bigram model.
# remove punctuations -print(string.punctuation) ---- !"#$%&'()*+,-./:;<=>?@[\]^_`{|}~ ----
# remove empty strings.
# lower case all the words
# add <s> at the beginning and </s> at the end of every sentence in the corpus.
# input - list of lists of words obtained from "tokenize_sentence" function.
# returns - list of lists
import string

def prep_data(lines):
    processed_lines = []
    for line in lines:
        # remove punctuation
        line = [word.translate(str.maketrans('', '', string.punctuation)) for word in line]
        # remove empty strings and convert to lower case
        line = [word.lower() for word in line if word]
        if line:
            # append </s> at the end and <s> at the beginning of each sentence
            line = ['<s>'] + line + ['</s>']
            processed_lines.append(line)
    print("No of sentences in Corpus: "+str(len(processed_lines)))
    return processed_lines
prep=prep_data(a)
prep

No of sentences in Corpus: 10033


[['<s>',
  ' ',
  'm',
  'o',
  'b',
  'y',
  ' ',
  'd',
  'i',
  'c',
  'k',
  ' ',
  'b',
  'y',
  ' ',
  'h',
  'e',
  'r',
  'm',
  'a',
  'n',
  ' ',
  'm',
  'e',
  'l',
  'v',
  'i',
  'l',
  'l',
  'e',
  ' ',
  '1',
  '8',
  '5',
  '1',
  ' ',
  '</s>'],
 ['<s>', 'e', 't', 'y', 'm', 'o', 'l', 'o', 'g', 'y', ' ', '</s>'],
 ['<s>',
  ' ',
  's',
  'u',
  'p',
  'p',
  'l',
  'i',
  'e',
  'd',
  ' ',
  'b',
  'y',
  ' ',
  'a',
  ' ',
  'l',
  'a',
  't',
  'e',
  ' ',
  'c',
  'o',
  'n',
  's',
  'u',
  'm',
  'p',
  't',
  'i',
  'v',
  'e',
  ' ',
  'u',
  's',
  'h',
  'e',
  'r',
  ' ',
  't',
  'o',
  ' ',
  'a',
  ' ',
  'g',
  'r',
  'a',
  'm',
  'm',
  'a',
  'r',
  ' ',
  's',
  'c',
  'h',
  'o',
  'o',
  'l',
  ' ',
  '</s>'],
 ['<s>',
  't',
  'h',
  'e',
  ' ',
  'p',
  'a',
  'l',
  'e',
  ' ',
  'u',
  's',
  'h',
  'e',
  'r',
  ' ',
  ' ',
  't',
  'h',
  'r',
  'e',
  'a',
  'd',
  'b',
  'a',
  'r',
  'e',
  ' ',
  'i',
  'n',
  ' ',
  'c',
  'o',
  'a',
 

In [ ]:
dataset = load_file(filename)
dataset = tokenize_sentence(dataset)
dataset = prep_data(dataset)

No of sentences in Corpus: 10033


In [ ]:
# Creates the vocabulary file of the dataset.
def vocabulary(dataset):
    dataset_vocab = set(itertools.chain.from_iterable(dataset))
    # remove <s> and </s> from the vocabulary of the dataset
   # dataset_vocab.remove('<s>')
    dataset_vocab.remove('</s>')
    dataset_vocab = list(dataset_vocab)
    dataset_vocab.append('<s>')
    dataset_vocab.append('</s>')
    return dataset_vocab

dataset_vocab = vocabulary(dataset)
dataset_vocab

['urn',
 'immensities',
 'padded',
 'provision',
 'calais',
 'casual',
 'unfrequented',
 'masked',
 'forethrown',
 'specksynder',
 'amorous',
 'fancy',
 'warlike',
 'crumpled',
 'hags',
 'bent',
 'cased',
 'pillaged',
 'pampered',
 'sickle',
 'ridiculous',
 'shy',
 'poisonous',
 'wrung',
 'vesture',
 'irregularity',
 'already',
 'ordered',
 'uppermost',
 'liability',
 'vestige',
 'quarto',
 'symbolize',
 'chamois',
 'bunched',
 'hitting',
 'prevailing',
 'lively',
 'dexterities',
 'heinousness',
 'movable',
 'nautical',
 'hospital',
 'subdivisions',
 'clinched',
 'ties',
 'biggest',
 'brotherly',
 'widow',
 'verbally',
 'encountered',
 'unfathomably',
 'mow',
 'intercourse',
 'flourished',
 'conceivable',
 'praying',
 'forges',
 'everyway',
 'sixth',
 'periodically',
 'interlacing',
 'cakes',
 'away',
 'renegades',
 'pivot',
 'regale',
 'hip',
 'investment',
 'redeemed',
 'distantly',
 '28',
 'persians',
 'marshy',
 'remoter',
 'unhinted',
 'metres',
 'scorchingly',
 'treble',
 'pallid

In [ ]:
len(dataset_vocab)

17142

In [ ]:
# Counts the no. of times a word repeats (frequency of each word) in the corpus.
# input - list of lists of words obtained from "prep_data"
# returns - a dictionary defined as {word:frequency} for words of the corpus including <s> and </s>.
def freq_of_unique_words(lines):
    count = {}
    for line in lines:
        for word in line:
            if word in count:
                count[word] += 1
            else:
                count[word] = 1
    unique_word_count = len(count)
    print("No of unique words in corpus : "+ str(unique_word_count))
    return count
freq=freq_of_unique_words(a)
freq

No of unique words in corpus : 54


{'[': 3,
 ' ': 250800,
 'm': 23277,
 'o': 69326,
 'b': 16877,
 'y': 16872,
 'd': 38219,
 'i': 65434,
 'c': 22507,
 'k': 8059,
 'h': 62896,
 'e': 117092,
 'r': 52134,
 'a': 77916,
 'n': 65617,
 'l': 42793,
 'v': 8598,
 '1': 142,
 '8': 59,
 '5': 55,
 ']': 3,
 't': 87996,
 'g': 20820,
 '.': 7558,
 '(': 215,
 's': 64231,
 'u': 26697,
 'p': 17255,
 ')': 215,
 '-': 5984,
 ',': 19229,
 ';': 4173,
 'w': 22222,
 'x': 1030,
 'q': 1556,
 'f': 20833,
 '"': 3071,
 "'": 2922,
 '!': 1767,
 'j': 1082,
 ':': 196,
 'z': 632,
 '9': 35,
 '0': 131,
 '6': 37,
 '7': 53,
 '2': 60,
 '?': 1004,
 '4': 39,
 '3': 47,
 '_': 26,
 '$': 2,
 '*': 45,
 '&': 2}

In [ ]:
unique_word_frequency = freq_of_unique_words(dataset)
len(unique_word_frequency)

No of unique words in corpus : 17141


17141

QUESTION 1A (5)

In [ ]:
# Computes the bigram frequncies
# Bigram frequncies means the number of times a word appears after a given word in the corpus.
# inputs:
# lines - list of lists obtained from "prep_data".
# count - dictionary obtained from "freq_of_unique_words".
# returns - dictionary of bigram frequencies {(word|given word): count(word|given word)} --- count(word|given word)~int.
def compute_bigram_frequencies(lines):
    bigram_frequencies = {}
    for line in lines:
        for i in range(len(line)-1):
            if (line[i], line[i+1]) in bigram_frequencies:
                bigram_frequencies[(line[i], line[i+1])] += 1
            else:
                bigram_frequencies[(line[i], line[i+1])] = 1
    print("The number of bigram frequencies in the corpus: "+ str(len(bigram_frequencies)))
    return bigram_frequencies
compute_bigram_frequencies(prep)

The number of bigram frequencies in the corpus: 709


{('<s>', ' '): 1423,
 (' ', 'm'): 8327,
 ('m', 'o'): 2918,
 ('o', 'b'): 573,
 ('b', 'y'): 1382,
 ('y', ' '): 12291,
 (' ', 'd'): 5735,
 ('d', 'i'): 2689,
 ('i', 'c'): 2763,
 ('c', 'k'): 2102,
 ('k', ' '): 2654,
 (' ', 'b'): 10441,
 (' ', 'h'): 13305,
 ('h', 'e'): 26514,
 ('e', 'r'): 14922,
 ('r', 'm'): 1066,
 ('m', 'a'): 3993,
 ('a', 'n'): 15160,
 ('n', ' '): 17437,
 ('m', 'e'): 5787,
 ('e', 'l'): 4018,
 ('l', 'v'): 213,
 ('v', 'i'): 1495,
 ('i', 'l'): 3722,
 ('l', 'l'): 6007,
 ('l', 'e'): 8417,
 ('e', ' '): 42668,
 (' ', '1'): 99,
 ('1', '8'): 27,
 ('8', '5'): 5,
 ('5', '1'): 4,
 ('1', ' '): 9,
 (' ', '</s>'): 9893,
 ('<s>', 'e'): 73,
 ('e', 't'): 3168,
 ('t', 'y'): 953,
 ('y', 'm'): 62,
 ('o', 'l'): 2385,
 ('l', 'o'): 3488,
 ('o', 'g'): 345,
 ('g', 'y'): 68,
 (' ', 's'): 19625,
 ('s', 'u'): 1908,
 ('u', 'p'): 1531,
 ('p', 'p'): 806,
 ('p', 'l'): 1256,
 ('l', 'i'): 4588,
 ('i', 'e'): 1996,
 ('e', 'd'): 9216,
 ('d', ' '): 23430,
 (' ', 'a'): 22896,
 ('a', ' '): 5608,
 (' ', 'l'): 5996,

In [ ]:
bigram_frequencies = compute_bigram_frequencies(dataset)
print(bigram_frequencies)
bigram_unique_word_count = len(unique_word_frequency)
print("\n"+"No of words in bigram: "+str(bigram_unique_word_count))

The number of bigram frequencies in the corpus: 114684
{('<s>', 'moby'): 5, ('moby', 'dick'): 84, ('dick', 'by'): 1, ('by', 'herman'): 1, ('herman', 'melville'): 1, ('melville', '1851'): 1, ('1851', '</s>'): 2, ('<s>', 'etymology'): 1, ('etymology', '</s>'): 1, ('<s>', 'supplied'): 1, ('supplied', 'by'): 2, ('by', 'a'): 82, ('a', 'late'): 1, ('late', 'consumptive'): 1, ('consumptive', 'usher'): 1, ('usher', 'to'): 1, ('to', 'a'): 113, ('a', 'grammar'): 1, ('grammar', 'school'): 1, ('school', '</s>'): 1, ('<s>', 'the'): 629, ('the', 'pale'): 4, ('pale', 'usher'): 1, ('usher', 'threadbare'): 1, ('threadbare', 'in'): 1, ('in', 'coat'): 1, ('coat', 'heart'): 1, ('heart', 'body'): 1, ('body', 'and'): 7, ('and', 'brain'): 1, ('brain', 'i'): 1, ('i', 'see'): 24, ('see', 'him'): 19, ('him', 'now'): 8, ('now', '</s>'): 47, ('<s>', 'he'): 264, ('he', 'was'): 144, ('was', 'ever'): 2, ('ever', 'dusting'): 1, ('dusting', 'his'): 1, ('his', 'old'): 14, ('old', 'lexicons'): 1, ('lexicons', 'and'): 1,

QUESTION 1B (5)

In [ ]:
# Calculating bigram probability
# bigram probability means P(word|given word) = count(word|given word)/ count(given word).
# if count(word|given word) or count(given word) is 0 then probability is 0.
# input bigram_frquencies and count obtained from "freq_of_unique_words".
# returns dictionary of bigram probabilities {(word|given word): probabilty} --- probability is a float value.
def compute_bigram_probabilities(bigram_frequencies, count):
    bigram_probabilities = {}
    for bigram in bigram_frequencies:
        given_word = bigram[0]
        bigram_probabilities[bigram] = bigram_frequencies[bigram] / count[given_word]
    return bigram_probabilities


In [ ]:
bigram_probabilities = compute_bigram_probabilities(bigram_frequencies,unique_word_frequency)
bigram_probabilities

{('<s>', 'moby'): 0.000498355427090601,
 ('moby', 'dick'): 1.0,
 ('dick', 'by'): 0.011904761904761904,
 ('by', 'herman'): 0.0008305647840531562,
 ('herman', 'melville'): 1.0,
 ('melville', '1851'): 1.0,
 ('1851', '</s>'): 0.6666666666666666,
 ('<s>', 'etymology'): 9.96710854181202e-05,
 ('etymology', '</s>'): 1.0,
 ('<s>', 'supplied'): 9.96710854181202e-05,
 ('supplied', 'by'): 0.16666666666666666,
 ('by', 'a'): 0.0681063122923588,
 ('a', 'late'): 0.00021114864864864866,
 ('late', 'consumptive'): 0.03333333333333333,
 ('consumptive', 'usher'): 1.0,
 ('usher', 'to'): 0.5,
 ('to', 'a'): 0.024432432432432434,
 ('a', 'grammar'): 0.00021114864864864866,
 ('grammar', 'school'): 0.5,
 ('school', '</s>'): 0.1,
 ('<s>', 'the'): 0.0626931127279976,
 ('the', 'pale'): 0.0002771810685330192,
 ('pale', 'usher'): 0.05263157894736842,
 ('usher', 'threadbare'): 0.5,
 ('threadbare', 'in'): 1.0,
 ('in', 'coat'): 0.00023969319271332693,
 ('coat', 'heart'): 0.03571428571428571,
 ('heart', 'body'): 0.010989

In [ ]:
# Bigram frequncies of the test sentence computed using the bigram frequencies of the training data.
# add-one smoothing if 1, no smoothing if 0 ----- smoothing
def compute_bigram_count_test_sentence(given_word,word,smoothing):
    if smoothing==0:
        return 0 if bigram_frequencies.get((given_word,word))==None else bigram_frequencies.get((given_word,word))
    elif smoothing == 1:
        return 1 if bigram_frequencies.get((given_word,word))==None else bigram_frequencies.get((given_word,word))+1

In [ ]:
# A table showing the bigram counts for test sentence.
def print_bigram_freq_test_sentence(test_sentence_vocab,smoothing):
    print("A table showing the bigram counts for test sentence."+"\nsmoothing ="+str(smoothing))
    print("\t\t\t", end="")
    for word in test_sentence_vocab:
        if word != '<s>':
            print(word, end="\t\t")
    print("")
    for given_word in test_sentence_vocab:
        if given_word != '</s>':
            if(smoothing==1):
                print(unique_word_frequency.get(given_word)+bigram_unique_word_count, end ="\t")
            elif(smoothing==0):
                print(unique_word_frequency.get(given_word), end ="\t")
            print(given_word, end="\t\t")
            for word in test_sentence_vocab:
                if word !='<s>':
                    print("{0:}".format(compute_bigram_count_test_sentence(given_word,word,smoothing)), end="\t\t")
            print("")
    print("")

In [ ]:
# Bigram probabilities of the test sentence computed using the bigram probabilities of the training data.
# add-one smoothing if 1, no smoothing if 0 ---- smoothing
def compute_bigram_prob_test_sentence(given_word,word,smoothing):
    bigram_freq = 0 if bigram_frequencies.get((given_word,word))==None else bigram_frequencies.get((given_word,word))
    uni_freq = 0 if unique_word_frequency.get((given_word))==None else unique_word_frequency.get((given_word))
    if smoothing==0:
        return 0 if bigram_probabilities.get((given_word,word))==None else bigram_probabilities.get((given_word,word))
    elif smoothing == 1:
        numerator = bigram_freq+1
        denominator = uni_freq+bigram_unique_word_count
        return 0.0 if numerator == 0 or denominator == 0 else float(numerator) / float(denominator)

QUESTION 1C (5)

In [ ]:
# A table showing the bigram probabilities for test sentence.
def print_bigram_probabilities_test_sentence(test_sentence_vocab, bigram_probabilities, smoothing):
    for i in range(len(test_sentence_vocab)-1):
        bigram = (test_sentence_vocab[i], test_sentence_vocab[i+1])
        if bigram in bigram_probabilities:
            print(f"Bigram: {bigram}, Probability: {bigram_probabilities[bigram]}")
        else:
            print(f"Bigram: {bigram}, Probability: {smoothing}")


In [ ]:
# Print the probability of the test sentence
# for add-one smoothing if 1, no smoothing if 0
def compute_prob_test_sentence(sentence, bigram_probabilities, count, smoothing):
    sentence_vocab = sentence.split()
    sentence_vocab = ['<s>'] + sentence_vocab + ['</s>']
    prob = 1
    for i in range(len(sentence_vocab)-1):
        bigram = (sentence_vocab[i], sentence_vocab[i+1])
        if bigram in bigram_probabilities:
            prob *= bigram_probabilities[bigram]
        else:
            if smoothing:
                prob *= 1 / (count[sentence_vocab[i]] + len(count))
            else:
                prob = 0
                break
    return prob


In [ ]:
# Test sentence here
test_sentences = [['upon this the captain started , and eagerly desired to know more .'],['thus , because no man can follow another into these halls .']]

In [ ]:
smoothing=1
for i in range (len(test_sentences)):
    test_sentence = test_sentences[i]
    print("!!!!!!!!!!The test Sentence is!!!!!!!!!!")
    print(test_sentence)
    test_sentence = tokenize_sentence(test_sentence)
    test_sentence = prep_data(test_sentence)

    # Vocabulary of test sentence
    test_sentence_vocab = vocabulary(test_sentence)

    test_sentence = list(itertools.chain.from_iterable(test_sentence))
    #test_sentence

    # A table showing the bigram counts for test sentence.
    print_bigram_freq_test_sentence(test_sentence_vocab,smoothing)

    # A table showing the bigram probabilities for test sentence.
    print_bigram_probabilities_test_sentence(test_sentence_vocab,smoothing)

    # The probability of the sentence under the trained model
    print("The probability of the sentence under the trained model"+"\nsmoothing ="+str(smoothing))
    print(compute_prob_test_sentence(test_sentence,0))

!!!!!!!!!!The test Sentence is!!!!!!!!!!
['upon this the captain started , and eagerly desired to know more .']
No of sentences in Corpus: 1
A table showing the bigram counts for test sentence.
smoothing =1
			the		more		upon		to		desired		this		eagerly		captain		know		started		and		</s>		
31572	the		1		51		1		1		4		1		1		98		1		1		1		2		
17649	more		15		1		3		12		1		1		1		1		1		2		25		26		
17707	upon		221		1		1		1		1		24		1		2		1		1		1		5		
21766	to		730		2		2		2		1		51		1		3		16		1		24		27		
17152	desired		1		1		1		3		1		1		1		1		1		1		1		1		
18535	this		25		1		1		8		1		2		1		2		1		1		10		26		
17149	eagerly		1		1		1		1		2		1		1		1		1		1		2		1		
17470	captain		4		1		2		9		1		3		1		1		1		2		12		11		
17293	know		9		2		1		2		1		1		1		2		1		1		3		8		
27174	<s>		630		8		27		61		1		116		1		23		3		2		409		1		
17168	started		2		1		1		6		1		1		1		1		1		1		2		1		
23571	and		371		46		3		31		1		45		3		6		2		2		1		1		
27174	<s>		630		8		27		61		1		116		1		23		3		2		409		1		



TypeError: ignored